
# Tutorial 08: Calculating equilibrium compositions of an SiO-CO plasma.

Calculations of plasmas arising from metallurgical processes are typically a
lot more complicated than single-element systems. For example the plasma in an
electric arc running above an oxide slag or sulphide matte in a smelting
furnace may have multiple metallic elements and their molecules present in
different proportions, together with carbon, oxygen, sulphur, and trace
impurities. To illustrate this let's consider the case of a carbon monoxide &
silicon monoxide plasma, such as one might obtain when heating pure
$SiO_2$ in a reducing environment with carbon present.

A small text file in the JSON format must be generated by the user to specify
the system. In this case we'll assume the presence of as many possible species
obtained by combining silicon, carbon, and oxygen as we have data for, but it's
important to be aware that such a "brute-force" approach may not always be the
most expedient as the number of species rises; the expertise of the user in
judging which species are of dominant importance in a particular plasma mixture
becomes valuable in such cases.

We'll go ahead and assume that all of $O_2, O_2^+, O, O^+, O^{2+}, SiO,
SiO^+, Si, Si^+, Si^{2+}, CO, CO^+, C, C^+, C^{2+}$ are present, and let's also
assume we are interested in the case of a plasma formed from a 50/50 mixture
(by mole) of CO and SiO. This composition constraint has the effect of fixing
the elemental make-up of the plasma using mole fractions of the two diatomic
species CO and SiO; what this really amounts to internally is telling
minplascalc that "at all times during the calculation of the composition, you
should have 1 atom of carbon and 1 atom of silicon for every 2 atoms of oxygen
regardless of their proportionation between different species", thereby
preserving the element balance for C, Si, and O.

In order to calculate the composition of the plasma at various temperatures
using these species, execute the following code snippets in order.
The text in between indicates what each part of the code is doing.


## Import the required libraries.

We start by importing the modules we need:

- matplotlib for drawing graphs,
- numpy for array functions,
- and of course minplascalc.



In [ ]:
import matplotlib.pyplot as plt
import numpy as np

import minplascalc as mpc

## Create mixture object for the species we're interested in.

Next, we create a minplascalc LTE mixture object, again using the helper
function in minplascalc which creates the object directly from a list of the
species names.



In [ ]:
species = [
    "O2",
    "O2+",
    "O",
    "O+",
    "O++",
    "CO",
    "CO+",
    "C",
    "C+",
    "C++",
    "SiO",
    "SiO+",
    "Si",
    "Si+",
    "Si++",
]
x0 = [0, 0, 0, 0, 0, 0.5, 0, 0, 0, 0, 0.5, 0, 0, 0, 0]
sico_mixture = mpc.mixture.lte_from_names(species, x0, 1000, 101325)

## Set a range of temperatures to calculate the equilibrium compositions at.

Next, set a range of temperatures to calculate the equilibrium compositions
at - in this case we're going from 1000 to 25000 K in 100 K steps.
Also initialise a list to store the composition result at each temperature



In [ ]:
temperatures = np.linspace(1000, 25000, 100)
species_names = [sp.name for sp in sico_mixture.species]
ni_list = []

## Perform the composition calculations.

Now we're ready to actually perform the composition calculations.
We loop over all the temperatures, setting the LTE object's temperature
attribute to the appropriate value, and calculating the composition using
the object's `calculate_composition()` function.

Note that execution of this calculation is fairly compute intensive (the more
species present the more intensive it becomes) and the following code snippet
may take a few tens of seconds to complete.



In [ ]:
for T in temperatures:
    sico_mixture.T = T
    ni_list.append(sico_mixture.calculate_composition())
ni = np.array(ni_list).transpose()

## Plot the results.

Now we can go ahead and visualise the results by plotting the plasma
composition against temperature, to see how it varies.



In [ ]:
fig, ax = plt.subplots(1, 1, figsize=(7, 4))

ax.set_title("50/50 SiO-CO LTE plasma, composition with temperature at 1 atm")
ax.set_xlabel("T [K]")
ax.set_ylabel(r"$\mathregular{n_i [m^{-3}]}$")
ax.set_ylim(1e15, 5e25)
for spn, sn in zip(ni, species_names):
    ax.semilogy(temperatures, spn, label=sn)
ax.legend(loc=(1.025, 0.25), ncols=2)

## Reducing the number of species to plot.

Whew, what a mess! It's hard to see what's going on in this complex plasma,
so let's pull out just the silicon species and the pure oxygen species.



In [ ]:
silicon_species = ["SiO", "SiO+", "Si", "Si+", "Si++"]
silicon_species_names = []
silicon_ni = []
for spn, sn in zip(ni, species_names):
    if sn in silicon_species:
        silicon_species_names.append(sn)
        silicon_ni.append(spn)
oxygen_species = ["O2", "O2+", "O", "O+", "O++"]
oxygen_species_names = []
oxygen_ni = []
for spn, sn in zip(ni, species_names):
    if sn in oxygen_species:
        oxygen_species_names.append(sn)
        oxygen_ni.append(spn)

Plotting those side by side we can start to see some more useful information.



In [ ]:
fig, axs = plt.subplots(2, 1, figsize=(7, 8), sharex=True)

ax = axs[0]
ax.set_title("50/50 SiO-CO LTE plasma - silicon species")
ax.set_ylabel(r"$\mathregular{n_i [m^{-3}]}$")
ax.set_ylim(1e15, 5e25)
for spn, sn in zip(silicon_ni, silicon_species_names):
    ax.semilogy(temperatures, spn, label=sn)
ax.legend(loc=(1.025, 0.25))

ax = axs[1]
ax.set_title("50/50 SiO-CO LTE plasma - oxygen species")
ax.set_xlabel("T [K]")
ax.set_ylabel(r"$\mathregular{n_i [m^{-3}]}$")
ax.set_ylim(1e15, 5e25)
for spn, sn in zip(oxygen_ni, oxygen_species_names):
    ax.semilogy(temperatures, spn, label=sn)
ax.legend(loc=(1.025, 0.25))

## Conclusion

That's a bit better. Now we can see that the general behaviour of SiO in this
mixture is quite similar to that of $O_2$ (see
`sphx_glr_auto_examples_plot_tutorial_05_oygen_plasma_lte_composition.py`),  # noqa: E501
with the difference that Si species are easier to ionise - this leads to
higher concentrations of charged ions, particularly at lower temperatures.

It also suggests that at higher temperatures, our calculation should probably
be including $Si^{3+}$ as well. Pure oxygen species are largely absent
from the plasma at low temperatures as one would expect (this is after all a
CO-SiO plasma with no stoichiometrically free oxygen), but as dissociation
and ionisation of the other species proceeds their concentrations rise and
start to contribute significantly to the plasma composition.

